In [0]:
# GOLD LAYER - KPIs
silver_path = "/Volumes/workspace/default/silver/hvfhs_tripdata"

df_silver = spark.read.parquet(silver_path)

df_silver.printSchema()
df_silver.display()

from pyspark.sql.functions import (
    count, sum, avg, col, to_date
)

df_kpi_daily = (
    df_silver
    .withColumn("trip_date", to_date("pickup_datetime"))
    .groupBy("trip_date")
    .agg(
        count("*").alias("total_trips"),
        sum("base_passenger_fare").alias("total_revenue"),
        avg("trip_miles").alias("avg_trip_miles"),
        avg("trip_time").alias("avg_trip_time"),
        sum("tips").alias("total_tips")
    )
    .orderBy("trip_date")
)

df_kpi_daily.display()

df_location_summary = (
    df_silver
    .groupBy("PULocationID")
    .agg(
        count("*").alias("total_trips"),
        sum("base_passenger_fare").alias("total_revenue"),
        avg("trip_miles").alias("avg_trip_miles"),
        avg("trip_time").alias("avg_trip_time")
    )
    .orderBy(col("total_trips").desc())
)

df_location_summary.display()

df_revenue_summary = (
    df_silver
    .agg(
        sum("base_passenger_fare").alias("total_base_fare"),
        sum("tolls").alias("total_tolls"),
        sum("bcf").alias("total_bcf"),
        sum("sales_tax").alias("total_sales_tax"),
        sum("congestion_surcharge").alias("total_congestion"),
        sum("airport_fee").alias("total_airport_fee"),
        sum("tips").alias("total_tips")
    )
)

df_revenue_summary.display()

spark.sql("""
CREATE VOLUME IF NOT EXISTS workspace.default.gold
""")

gold_path = "/Volumes/workspace/default/gold"

df_kpi_daily.write.mode("overwrite").parquet(f"{gold_path}/kpi_daily")
df_location_summary.write.mode("overwrite").parquet(f"{gold_path}/location_summary")
df_revenue_summary.write.mode("overwrite").parquet(f"{gold_path}/revenue_summary")



root
 |-- pickup_datetime: timestamp_ntz (nullable = true)
 |-- dropoff_datetime: timestamp_ntz (nullable = true)
 |-- PULocationID: integer (nullable = true)
 |-- DOLocationID: integer (nullable = true)
 |-- trip_miles: double (nullable = true)
 |-- trip_time: long (nullable = true)
 |-- base_passenger_fare: double (nullable = true)
 |-- tolls: double (nullable = true)
 |-- bcf: double (nullable = true)
 |-- sales_tax: double (nullable = true)
 |-- congestion_surcharge: double (nullable = true)
 |-- airport_fee: double (nullable = true)
 |-- tips: double (nullable = true)
 |-- cbd_congestion_fee: double (nullable = true)
 |-- ingestion_timestamp: timestamp (nullable = true)



pickup_datetime dropoff_datetime PULocationID DOLocationID trip_miles trip_time base_passenger_fare tolls bcf sales_tax congestion_surcharge airport_fee tips cbd_congestion_fee ingestion_timestamp 2025-01-15T14:18:34.000 2025-01-15T14:27:35.000 162 237 1.0 541 33.22 0.0 0.87 2.94 2.75 0.0 7.95 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:34:33.000 2025-01-15T15:06:58.000 162 33 7.03 1945 73.11 0.0 1.97 6.49 2.75 0.0 8.43 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:36:46.000 2025-01-15T14:45:38.000 233 141 1.008 532 10.29 0.0 0.28 0.91 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:01:59.000 2025-01-15T14:11:58.000 236 141 1.29 599 12.71 0.0 0.35 1.13 2.75 0.0 3.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:25:54.000 2025-01-15T15:22:44.000 262 132 18.98 3410 86.21 6.94 2.44 8.49 2.75 2.5 16.19 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:22:05.000 2025-01-15T14:46:18.000 261 246 3.39 1453 31.22 0.0 0.82 2.77 2.75 0.0 3.75 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:59:22.000 2025-01-15T15:20:06.000 90 232 2.91 1244 25.32 0.0 0.65 2.25 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:25:04.000 2025-01-15T14:33:18.000 226 7 1.053 494 9.67 0.0 0.27 0.86 0.0 0.0 5.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:18:10.000 2025-01-15T14:28:22.000 142 142 0.849 612 13.26 0.0 0.36 1.18 2.75 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:42:20.000 2025-01-15T14:59:11.000 143 186 2.535 1011 13.22 0.0 0.36 1.17 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:18:12.000 2025-01-15T14:40:04.000 26 40 4.1 1312 23.29 0.0 0.64 2.06 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:43:20.000 2025-01-15T15:09:44.000 40 170 8.97 1584 51.66 6.94 1.37 5.2 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:35:33.000 2025-01-15T14:45:56.000 82 83 1.6 623 7.2 0.0 0.21 0.68 0.0 0.0 1.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:16:22.000 2025-01-15T14:27:29.000 82 157 1.68 667 13.41 0.0 0.37 1.19 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:30:17.000 2025-01-15T14:42:41.000 157 260 1.38 744 11.64 0.0 0.32 1.04 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:03:23.000 2025-01-15T14:11:37.000 207 82 1.458 494 9.59 0.0 0.26 0.85 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:14:39.000 2025-01-15T14:26:26.000 144 158 1.7 707 29.56 0.0 0.75 2.57 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:56:29.000 2025-01-15T15:09:51.000 158 231 1.8 802 25.41 0.0 0.65 2.26 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:03:27.000 2025-01-15T14:15:17.000 237 236 1.67 710 10.92 0.0 0.3 0.97 2.75 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:27:57.000 2025-01-15T14:38:40.000 262 237 1.32 643 16.9 0.0 0.47 1.51 2.75 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:55:04.000 2025-01-15T15:07:23.000 141 236 0.88 739 12.57 0.0 0.34 1.11 2.75 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:54:52.000 2025-01-15T15:22:48.000 121 139 6.12 1676 26.5 0.0 0.71 2.28 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:48:07.000 2025-01-15T15:14:21.000 246 181 6.79 1574 57.3 6.94 1.53 5.7 2.75 0.0 14.84 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:13:36.000 2025-01-15T14:39:08.000 161 107 1.92 1532 25.33 0.0 0.65 2.25 2.75 0.0 4.64 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:15:00.000 2025-01-15T14:33:16.000 137 237 2.14 1096 20.69 0.0 0.53 1.84 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:39:06.000 2025-01-15T15:26:31.000 236 181 9.92 2845 37.78 0.0 1.04 3.34 2.75 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:33:58.000 2025-01-15T14:49:34.000 211 137 2.37 936 25.29 0.0 0.65 2.23 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:52:15.000 2025-01-15T15:16:50.000 137 97 6.21 1475 32.43 0.0 0.85 2.88 2.75 0.0 0.0 1.5 2026-01-29T00:51:19.444Z 2025-01-15T14:18:49.000 2025-01-15T14:29:32.000 108 108 1.83 643 10.76 0.0 0.29 0.96 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z 2025-01-15T14:38:03.000 2025-01-15T15:18:31.000 123 62 6.34 2428 37.84 0.0 1.11 3.57 0.0 0.0 0.0 0.0 2026-01-29T00:51:19.444Z

trip_date total_trips total_revenue avg_trip_miles avg_trip_time total_tips 2025-01-01 2654252 7.566860640000153E7 5.484956959625669 1055.5073112876998 2846462.08000002 2025-01-02 2116952 5.220691184000116E7 5.018121051398382 1082.2391589417239 2165852.080000105 2025-01-03 2451160 5.763071628000269E7 4.801711907831435 1081.8494590316423 2359468.160000078 2025-01-04 2689404 6.092353800000359E7 4.896543431927767 1055.6826880602543 2755653.639999997 2025-01-05 2343360 5.4577525640000604E7 5.264706906322563 1028.1198040420593 2414821.600000068 2025-01-06 2251532 5.3680415320001125E7 4.823054471355674 1072.6561292488848 2348822.0400000713 2025-01-07 2434128 5.7817337799999826E7 4.5987986630119195 1068.0270519874057 2593155.2400000426 2025-01-08 2564108 6.117559331999966E7 4.563608436150147 1082.0163534453307 2785686.9999998603 2025-01-09 2748200 6.6040522159997255E7 4.627143905101539 1096.8879994178008 2950318.640000068 2025-01-10 2855884 6.761904199999963E7 4.673949268247623 1098.1999212853184 2833305.0400000233 2025-01-11 3016224 6.78594537199999E7 4.767927392660467 1041.281919379993 2881179.7199999653 2025-01-12 2534544 5.9183567120002E7 5.227825074648597 1036.767227556515 2434112.4400000693 2025-01-13 2295020 5.694586920000203E7 4.886720352763842 1094.0823957961152 2574829.320000044 2025-01-14 2463228 6.185636388000149E7 4.6935816741283 1108.0970709978938 2805667.0000000224 2025-01-15 2627904 6.6807768559998654E7 4.768258975974783 1129.8030643432942 2996994.2400000556 2025-01-16 2748440 7.206274947999504E7 4.955827672425079 1163.486922035773 3107100.1599997943 2025-01-17 2908200 7.16187503199943E7 4.8810910666392715 1169.2565091809367 2887912.3199997977 2025-01-18 3029464 6.780979103999643E7 4.809750464108575 1091.490906642231 2815527.0399999553 2025-01-19 2642116 5.9855776640002966E7 4.836554399579891 1015.5587445819941 2379459.920000068 2025-01-20 2285036 5.4236677159998104E7 5.167044655751631 1027.9431518803206 2339647.800000047 2025-01-21 2638256 6.443665591999528E7 4.657712767828386 1082.0447431939888 2905020.840000042 2025-01-22 2744844 6.751027747999844E7 4.54442280581352 1084.8551057910759 3030473.7199999844 2025-01-23 2793340 7.240569435999565E7 4.791433896338971 1141.760009164656 3258449.679999975 2025-01-24 3018540 7.302848563999401E7 4.685473757511997 1134.1874522119965 3064696.399999997 2025-01-25 3166320 7.226857995999053E7 4.6787058806437845 1081.3429179615453 2962881.720000071 2025-01-26 2627416 6.208378035999763E7 5.21534194356741 1052.0556227106786 2435977.3600000087 2025-01-27 2285440 5.641410867999816E7 4.958169507840968 1122.3793405208626 2428730.8800000153 2025-01-28 2412680 5.9099993079997964E7 4.745125672695863 1115.3124475686789 2637532.2400000184 2025-01-29 2470064 6.179785027999535E7 4.900581623796059 1108.8303687677728 2819075.239999976 2025-01-30 2747860 7.150315815999606E7 4.934937097231982 1178.491851841069 3162353.3999999836 2025-01-31 3058748 7.450995615999492E7 4.73238994255156 1159.3394826903034 3009983.639999984

PULocationID total_trips total_revenue avg_trip_miles avg_trip_time 132 1466144 9.634572264000049E7 18.34757717113739 2512.0170897265207 138 1444880 7.662492752000035E7 11.438551500470625 1760.447098721001 61 1061572 2.0784992640000284E7 3.6306086219305125 1078.803924745566 79 1023968 2.514585644000024E7 4.166942806806456 1045.075154692334 230 983356 3.6304951720000446E7 6.025785831377455 1302.2988541281081 161 957148 3.412477640000038E7 5.197266036182486 1239.9820006937275 231 918828 2.7510715920000356E7 4.719796231721276 1097.3603068256518 234 885244 2.5164290600000314E7 4.314297025452861 1104.5924739393884 37 873412 1.817327032000019E7 3.9236732355405954 1119.6875976057117 76 872192 1.5441530720000247E7 3.8447130402480063 973.421145802759 68 867352 2.70481922000001E7 5.122724337985039 1213.857732500761 246 849012 2.48265153600003E7 4.312118179719473 1108.5941023212863 181 824048 1.8399478200000398E7 4.138320476477103 1108.2510873153021 164 799856 2.5043175360000316E7 5.233540637314706 1177.922411033986 148 785716 2.074035004000019E7 4.575585473631705 1073.2436249230002 255 783204 1.891382156000027E7 4.164790072573689 1109.78143114693 48 779816 2.2733458680000294E7 5.398831929583378 1191.6924402679606 7 776824 1.5036575920000292E7 4.277081722500849 967.3048412510427 112 763812 1.680784780000022E7 4.011022869501928 1050.677653663467 249 743624 1.9324951080000173E7 3.92332186158596 1039.9252955794864 42 740344 1.4252941520000163E7 4.2500809839750255 953.2282020250046 170 739040 2.070724384000022E7 4.798757967092438 1107.6509417622863 17 686696 1.313595572000008E7 3.426994349755936 1036.6171406270023 237 685464 1.9937887360000163E7 4.234601893024297 1101.5140984792783 256 680436 1.5550758720000101E7 4.034353714383126 1082.9114097431648 89 669712 1.3630271160000088E7 4.162183708818112 1131.6820364574623 163 658532 2.333896384000012E7 5.210245813415287 1254.3907296835994 225 648116 1.3284247040000074E7 3.75102350813743 1130.8618148603027 36 642592 1.316478404000011E7 3.885158981126424 1071.5355933469448 244 640448 1.394443276000008E7 5.2743051551414215 1038.6391213650445 162 636928 2.1557782280000202E7 5.376091325864136 1212.9561959907555 145 636472 1.4062571960000107E7 4.631245044558115 1081.3598147286918 188 636016 1.2474971600000072E7 3.719864695227799 1107.1036766370657 129 635176 1.1662932560000129E7 3.9895361474614863 956.5315503104651 107 632108 1.6115390720000125E7 4.247710144468998 1060.4834680149595 236 630440 1.7485486200000063E7 4.52699237992513 1113.000564684982 130 614404 1.184692880000004E7 4.6890351104484855 1005.9926693185591 39 596716 1.0673789880000032E7 3.7937646853779654 949.1443433727268 80 596160 1.271016088000006E7 4.019866794149203 1041.8579106280192 82 588520 1.049716496000002E7 3.8600290219533764 961.7894922857337 74 575796 1.0982785000000013E7 4.304109184502837 975.3101376181842 142 559224 1.6214709600000111E7 4.898735233108736 1157.4368839677838 144 556320 1.5076874200000072E7 4.0851199813057235 1060.235260281852 90 551756 1.4937163600000057E7 4.34793790733584 1085.4611748671514 141 550740 1.419194848000007E7 4.5962098267785 1103.6644514653012 95 547064 1.1100914560000041E7 4.564607987365276 990.6085723059825 41 546928 1.1198194480000049E7 4.152322762776823 1004.5398882485446 75 545692 1.2218803840000007E7 4.871911092704306 1100.613144411133 239 528164 1.4424191520000083E7 4.950156140895635 1129.646291682129 97 524172 1.1653300720000027E7 4.099125630518231 1113.1785215539937 216 521924 9298487.959999925 4.000713337574044 861.2029797441774 168 519720 9808732.44000002 4.342604587085353 986.5120218579235 198 512972 1.0289364960000038E7 3.96728240917633 1075.9661424015346 114 508016 1.3489756440000065E7 4.0729272542596995 1047.8834682372208 140 507856 1.3635239800000018E7 5.437613410100512 1234.6379524904698 226 500860 9742907.439999979 4.100554150860527 1018.5360220420877 186 499944 1.5577667760000084E7 5.360577864720854 1240.2960651592978 49 495744 1.0648882799999991E7 3.8016993609605034 1082.9159808288

total_base_fare total_tolls total_bcf total_sales_tax total_congestion total_airport_fee total_tips 1.9806355159605627E9 8.38210157198951E7 5.4330933200109236E7 1.664860981998389E8 8.2591741E7 1.540655836E7 8.49911506000032E7